In [46]:
import re
import sys
sys.path.append('../')
import os
import pandas as pd
from collections import Counter
import datetime

pd.set_option('display.max_rows', None)

SETTING_PARAMS = {
    'Apache': {
        'log_file': './logs/Apache/Apache_full.log',
        'log_template': './logs/Apache/Apache_full.log_templates.csv',
        'log_structure': './logs/Apache/Apache_full.log_structured.csv',
        'log_format': '\[<Time>\] \[<Level>\] <Content>',
        'filters': [],
        'regexs': [r'\/(?:\w+\/){2,}\w+\.\w+$'],    
    },
    'HealthApp':{
        'log_file': './logs/HealthApp/HealthApp_full.log',
        'log_template': './logs/HealthApp/HealthApp_full.log_templates.csv',
        'log_structure': './logs/HealthApp/HealthApp_full.log_structured.csv',
        'log_format': '<Time>\|<Component>\|<Pid>\|<Content>',
        'filters': [],
        'regexs': [],  
    },
    'Mac': {
        'log_file': './logs/Mac/Mac_full.log',
        'log_template': './logs/Mac/Mac_full.log_templates.csv',
        'log_structure': './logs/Mac/Mac_full.log_structured.csv',
        'log_format': '<Month>  <Date> <Time> <User> <Component>\[<PID>\]( \(<Address>\))?: <Content>',
        'filters': [],
        'regexs': [r'([\w-]+\.){2,}[\w-]+'],  
    },
    'Linux': {
        'log_file': './logs/Linux/Linux_full.log',
        'log_template': './logs/Linux/Linux_full.log_templates.csv',
        'log_structure': './logs/Linux/Linux_full.log_structured.csv',
        'log_format': '<Month> <Date> <Time> <Level> <Component>(\[<PID>\])?: <Content>',
        'filters': [],
        'regexs': [r'(\d+\.){3}\d+', r'\d{2}:\d{2}:\d{2}'],  
    },
    'OpenSSH': {
        'log_file': './logs/OpenSSH/OpenSSH_full.log',
        'log_template': './logs/OpenSSH/OpenSSH_full.log_templates.csv',
        'log_structure': './logs/OpenSSH/OpenSSH_full.log_structured.csv',
        'log_format': '<Date> <Day> <Time> <Component> sshd\[<Pid>\]: <Content>',
        'filters': [],
        'regexs': [r"(\d+):"],    
    },
}

In [ ]:
# ============ Các phương thức sử dụng ============ #
def log_to_dataframe(log_file, regex, headers):
    """ Phương thức chuyển đổi file log thành dataframe
    """
    log_messages = []
    linecount = 0
    with open(log_file, 'r', encoding="utf8") as fin:
        for line in fin.readlines():
            try:
                match = regex.search(line.strip())
                message = [match.group(header) for header in headers]
                log_messages.append(message)
                linecount += 1
            except Exception as e:
                pass
    logdf = pd.DataFrame(log_messages, columns=headers)
    logdf.insert(0, 'LineId', None)
    logdf['LineId'] = [i + 1 for i in range(linecount)]
    return logdf

def generate_logformat_regex(logformat):
    """ Phương thức tạo regex từ logformat, biểu thức định dạng của một event log: 
    Ex: 'log_format': '<Date> <Time> <Pid> <Level> <Component>: <Content>'
    """
    headers = []
    splitters = re.split(r'(<[^<>]+>)', logformat)
    regex = ''
    for k in range(len(splitters)):
        if k % 2 == 0:
            splitter = re.sub(' +', '\\\s+', splitters[k])
            regex += splitter
        else:
            header = splitters[k].strip('<').strip('>')
            regex += '(?P<%s>.*?)' % header
            headers.append(header)
    regex = re.compile('^' + regex + '$')
    return headers, regex

def hasNumbers(s):
    return any(char.isdigit() for char in s)

def preprocess(line, regexs = [], filters = []):
    for currentFil in filters:
            line = re.sub(currentFil, '', line)
    for currentRex in regexs:
        line = re.sub(currentRex, "<*>", line)
    
    tokens = line.strip().split()
    # new_tokens = []
    # for token in tokens:
    #     if hasNumbers(token):
    #         new_tokens.append("<*>")
    #     else:
    #         new_tokens.append(token)
    # return " ".join(new_tokens)
    return " ".join(tokens)

# ============ Tùy chỉnh ============ #

def read_csv_to_dataframe(file_path, delimiter=','):
    """
    Đọc file CSV thành DataFrame với delimiter tùy chọn.

    Args:
        file_path (str): Đường dẫn tới file CSV.
        delimiter (str): Dấu phân tách giữa các cột (default là ',').

    Returns:
        DataFrame: Kết quả đọc từ CSV.
    """
    df = pd.read_csv(file_path, delimiter=delimiter)
    return df


In [ ]:
# --------------- Test với HealthApp --------------- #
log_headers, log_regex = generate_logformat_regex(SETTING_PARAMS['HealthApp']['log_format'])
logdf = log_to_dataframe(SETTING_PARAMS['HealthApp']['log_file'], log_regex, log_headers)
logdf['Template'] = logdf['Content'].apply(lambda x: preprocess(x, regexs=SETTING_PARAMS['HealthApp']['regexs'], filters=SETTING_PARAMS['HealthApp']['filters']))


print("Logdf shape: ", logdf.shape)

unique_templates = logdf['Template'].drop_duplicates()
edit_temp_df = pd.DataFrame(unique_templates.tolist(), columns=['EventTemplate'])
edit_temp_df['Length'] = edit_temp_df['EventTemplate'].apply(lambda x: len(x.split()))
edit_temp_df = edit_temp_df.sort_values(by=['Length', 'EventTemplate'])
for index, row in edit_temp_df.iterrows():
    print(f"Length: {row['Length']:02d}, Template: {row['EventTemplate']}")

In [ ]:
template_df = read_csv_to_dataframe(SETTING_PARAMS['HealthApp']['log_template'])
template_df['Length'] = template_df['EventTemplate'].apply(lambda x: len(x.split()))
template_df = template_df.sort_values(by=['Length', 'EventTemplate'])
print("Template df shape: ", template_df.shape)
for index, row in template_df.iterrows():
    print(f"Length: {row['Length']:02d}, Template: {row['EventTemplate']}")

In [ ]:
# --------------- Test với OpenSSH --------------- #
log_headers, log_regex = generate_logformat_regex(SETTING_PARAMS['OpenSSH']['log_format'])
logdf = log_to_dataframe(SETTING_PARAMS['OpenSSH']['log_file'], log_regex, log_headers)
logdf['Template'] = logdf['Content'].apply(lambda x: preprocess(x, regexs=SETTING_PARAMS['OpenSSH']['regexs'], filters=SETTING_PARAMS['OpenSSH']['filters']))


print("Logdf shape: ", logdf.shape)

unique_templates = logdf['Template'].drop_duplicates()
edit_temp_df = pd.DataFrame(unique_templates.tolist(), columns=['EventTemplate'])
edit_temp_df['Length'] = edit_temp_df['EventTemplate'].apply(lambda x: len(x.split()))
edit_temp_df = edit_temp_df.sort_values(by=['Length', 'EventTemplate'])

print("Logdf shape: ", edit_temp_df.shape)
for index, row in edit_temp_df.iterrows():
    print(f"Length: {row['Length']:02d}, Template: {row['EventTemplate']}")

In [ ]:
template_df = read_csv_to_dataframe(SETTING_PARAMS['OpenSSH']['log_template'])
template_df['Length'] = template_df['EventTemplate'].apply(lambda x: len(x.split()))
template_df = template_df.sort_values(by=['Length', 'EventTemplate'])
print("Template df shape: ", template_df.shape)
for index, row in template_df.iterrows():
    print(f"Length: {row['Length']:02d}, Template: {row['EventTemplate']}")

In [ ]:
# --------------- Test với Linux --------------- #
log_headers, log_regex = generate_logformat_regex(SETTING_PARAMS['Linux']['log_format'])
logdf = log_to_dataframe(SETTING_PARAMS['Linux']['log_file'], log_regex, log_headers)
logdf['Template'] = logdf['Content'].apply(lambda x: preprocess(x, regexs=SETTING_PARAMS['Linux']['regexs'], filters=SETTING_PARAMS['Linux']['filters']))


print("Logdf shape: ", logdf.shape)

unique_templates = logdf['Template'].drop_duplicates()
edit_temp_df = pd.DataFrame(unique_templates.tolist(), columns=['EventTemplate'])
edit_temp_df['Length'] = edit_temp_df['EventTemplate'].apply(lambda x: len(x.split()))
edit_temp_df = edit_temp_df.sort_values(by=['Length', 'EventTemplate'])

print("Logdf shape: ", edit_temp_df.shape)
for index, row in edit_temp_df.iterrows():
    print(f"Length: {row['Length']:02d}, Template: {row['EventTemplate']}")

In [ ]:
template_df = read_csv_to_dataframe(SETTING_PARAMS['Linux']['log_template'])
template_df['Length'] = template_df['EventTemplate'].apply(lambda x: len(x.split()))
template_df = template_df.sort_values(by=['Length', 'EventTemplate'])
print("Template df shape: ", template_df.shape)
for index, row in template_df.iterrows():
    print(f"Length: {row['Length']:02d}, Template: {row['EventTemplate']}")

In [ ]:
# --------------- Test với Mac --------------- #
log_headers, log_regex = generate_logformat_regex(SETTING_PARAMS['Mac']['log_format'])
logdf = log_to_dataframe(SETTING_PARAMS['Mac']['log_file'], log_regex, log_headers)
logdf['Template'] = logdf['Content'].apply(lambda x: preprocess(x, regexs=SETTING_PARAMS['Mac']['regexs'], filters=SETTING_PARAMS['Mac']['filters']))


print("Logdf shape: ", logdf.shape)

unique_templates = logdf['Template'].drop_duplicates()
edit_temp_df = pd.DataFrame(unique_templates.tolist(), columns=['EventTemplate'])
edit_temp_df['Length'] = edit_temp_df['EventTemplate'].apply(lambda x: len(x.split()))
edit_temp_df = edit_temp_df.sort_values(by=['Length', 'EventTemplate'])

print("Logdf shape: ", edit_temp_df.shape)
for index, row in edit_temp_df.iterrows():
    print(f"Length: {row['Length']:02d}, Template: {row['EventTemplate']}")

In [ ]:
template_df = read_csv_to_dataframe(SETTING_PARAMS['Mac']['log_template'])
template_df['Length'] = template_df['EventTemplate'].apply(lambda x: len(x.split()))
template_df = template_df.sort_values(by=['Length', 'EventTemplate'])
print("Template df shape: ", template_df.shape)
for index, row in template_df.iterrows():
    print(f"Length: {row['Length']:02d}, Template: {row['EventTemplate']}")

#### **Viết lại các phương thức được sử dụng để tiền xử lý:**
##### **1. pre_hasNumbers**
##### **2. pre_regexAndFilter**

In [ ]:
def pre_hasNumbers(s):
    return any(char.isdigit() for char in s)

def pre_regexAndFilter(line, regexs = [], filters = []):
    for currentFil in filters:
        line = re.sub(currentFil, '', line)
    for currentRex in regexs:
        line = re.sub(currentRex, "<*>", line)
    
    tokens = line.strip().split()
    return tokens

#### **Viết các phương thức xử lý theo nhóm:**
##### **1. handle_delimiterSpecial**

In [ ]:
# def handle_delimiterSpecial(line, token, specialDelimiter=['=', ':']):



#### **Nhóm các log lại với nhau để kiểm tra lỗi sai trong các nhóm sau khi sử dụng tiền xử lý:**
Ta sẽ nhóm theo dạng: 
- Template chuẩn 
- Các template được trích xuất sau chuẩn bằng cách gọi đến file ***_full.log_structured.csv
Dựa trên các nhóm log, ta sẽ kiểm tra lỗi sai của từng nhóm.

In [41]:
from tqdm import tqdm

def compare_templates(datasets):
    """ So sánh các mẫu log (EventTemplate) giữa dữ liệu ground truth và dữ liệu đã phân tích.

    Hàm này thực hiện các bước:
    - Đọc dữ liệu structured log (ground truth) và template chuẩn từ file.
    - Phân tích file log thô (`log_file`) bằng regex để sinh dataframe `parse_df`.
    - Áp dụng tiền xử lý để tạo cột `ParseTemplate` từ nội dung log (`Content`).
    - So sánh từng mẫu log đúng (`EventTemplate`) trong `structured_df` với các kết quả đã phân tích trong `parse_df`.
    - Lưu thông tin so sánh gồm: template gốc, danh sách template phân tích được, chỉ số dòng, và số lượng.

    Args:
        datasets (dict): Một dictionary chứa các đường dẫn và cấu hình sau:
            - 'log_structure' (str): Đường dẫn đến file CSV chứa log đã được gán EventTemplate (ground truth).
            - 'log_template' (str): Đường dẫn đến file CSV chứa danh sách các EventTemplate chuẩn.
            - 'log_file' (str): Đường dẫn đến file log thô để phân tích.
            - 'log_format' (str): Định dạng log (logformat) để tạo regex.
            - 'regexs' (List[str]): Danh sách regex để tiền xử lý nội dung log.
            - 'filters' (List[str]): Danh sách các từ khóa cần lọc trước khi phân tích template.

    Returns:
        tuple: 
            - template_compare (dict): Dictionary chứa thông tin so sánh theo cấu trúc:
                {
                    hash_template: {
                        'ground_truth': str,           # Template gốc từ ground truth
                        'parse': List[str],            # Danh sách các template được phân tích
                        'index': List[int],            # Danh sách chỉ số dòng tương ứng trong structured_df
                        'length': int                  # Số lượng dòng có template này
                    }
                }
            - structured_df (pd.DataFrame): DataFrame log với ground truth templates.
            - parse_df (pd.DataFrame): DataFrame log đã được phân tích.

    Raises:
        AssertionError: Nếu số lượng hoặc nội dung `EventTemplate` trong `structured_df` không khớp với `template_df`.

    Examples:
        >>> datasets = {
        ...     'log_structure': 'data/HDFS/structured_log.csv',
        ...     'log_template': 'data/HDFS/templates.csv',
        ...     'log_file': 'data/HDFS/HDFS.log',
        ...     'log_format': '<Date> <Time> <Pid> <Level> <Component>: <Content>',
        ...     'regexs': [r'blk_-?\d+', r'\d+\.\d+\.\d+\.\d+'],
        ...     'filters': ['INFO']
        ... }
        >>> template_compare, structured_df, parse_df = compare_templates(datasets)
        >>> print(template_compare[hash('Receiving block blk_-12345')])
        {
            'ground_truth': 'Receiving block blk_-12345',
            'parse': ['Receiving block <*>'],
            'index': [10, 25, 78],
            'length': 3
        }
    """
    structured_df = read_csv_to_dataframe(datasets['log_structure'])
    template_df = read_csv_to_dataframe(datasets['log_template'])
    
    # =============== Thực hiện phân tích parse thông qua các phương thức: ===============
    # 1. Phân tích thông qua tiền xử lý:
    print("Giai đoạn tiền xử lý:")
    log_headers, log_regex = generate_logformat_regex(datasets['log_format'])
    parse_df = log_to_dataframe(datasets['log_file'], log_regex, log_headers)
    parse_df['ParseTemplate'] = parse_df['Content'].apply(lambda x: preprocess(x, regexs=datasets['regexs'], filters=datasets['filters']))
    print("Shape: ", parse_df.shape)
    # ================ Kết thúc giai đoạn tiền xử lý ================
    
    # Kiểm tra xem template trong structed_df có tồn tại trong template_df không
    unique_templates = structured_df['EventTemplate'].unique()
    print("Số lượng template: ", len(unique_templates))
    assert len(unique_templates) == len(template_df), "Số lượng template không khớp"
    for row in unique_templates:
        if row not in template_df['EventTemplate'].values:
            assert False, f"Template {row} not found in template_df"

    # =============== Trích xuất các template từ DataFrame ===============
    template_compare = {}

    for template in tqdm(unique_templates, desc="Processing templates"):
        arr_index = structured_df[structured_df['EventTemplate'] == template].index.tolist()
        parse_template_series = parse_df.loc[arr_index, 'ParseTemplate']
        parse_template_unique = parse_template_series.unique().tolist()

        hash_key = hash(template)
        template_compare[hash_key] = {
            'ground_truth': template,
            'parse': parse_template_unique,
            'index': arr_index,
            'length': len(template.strip().split()),
            'nums': len(arr_index)
        }
    # =============== Kết thúc giai đoạn trích xuất template ===============
    
    return template_compare, structured_df, parse_df


# def print_template_compare(template_compare):
#     """
#     In ra nội dung của template_compare theo thứ tự sắp xếp:
#     - Ưu tiên theo độ dài của ground_truth (length tăng dần)
#     - Sau đó theo thứ tự từ điển của ground_truth

#     Args:
#         template_compare (dict): Dictionary chứa kết quả so sánh template.
#     """
#     # Chuyển dict thành list các tuple (hash_key, nội dung) để sắp xếp
#     sorted_items = sorted(
#         template_compare.items(),
#         key=lambda item: (item[1]['length'], item[1]['ground_truth'])
#     )

#     print(f"{'No.':<5} {'Len':<5} {'Nums':<8} {'Ground Truth':<100} {'Parse Templates'}")
#     print('-' * 120)
    
#     for i, (key, value) in enumerate(sorted_items, 1):
#         print(f"{i:<5} {value['length']:<5} {value['nums']:<8} {value['ground_truth']:<100} {value['parse']}")

def print_template_compare(template_compare):
    """
    In nội dung của template_compare theo định dạng rõ ràng:
    - Mỗi template là một block gồm: số thứ tự, ground truth, parse templates, độ dài, số lần xuất hiện.
    - Sắp xếp theo độ dài chuỗi ground truth và sau đó là giá trị ground truth.

    Args:
        template_compare (dict): Dictionary chứa kết quả so sánh template.
    """
    sorted_items = sorted(
        template_compare.items(),
        key=lambda item: (item[1]['length'], item[1]['ground_truth'])
    )

    for idx, (key, value) in enumerate(sorted_items, 1):
        print(f"No. {idx}")
        print(f"Ground truth  : {value['ground_truth']}")
        print(f"Parse templs  : {value['parse']}")
        print(f"Length: {value['length']}, Nums: {value['nums']}")
        print("-" * 40)
        
def print_template_compare_difference(template_compare):
    sorted_items = sorted(
        template_compare.items(),
        key=lambda item: (item[1]['length'], item[1]['ground_truth'])
    )

    num_dif = 0
    for idx, (key, value) in enumerate(sorted_items, 1):
        if len(value['parse']) != 1 or value['parse'][0] != value['ground_truth']:
            num_dif += 1
            print(f"No. {idx}")
            print(f"Length: {value['length']}, Nums: {value['nums']}")
            print(f"Ground truth  : {value['ground_truth']}")
            print(f"Parse templs  : {value['parse']}")
            print(f"Length parse: {len(value['parse'])}")
            print("-" * 40)
    print(f"Total differences found: {num_dif}")

In [45]:
# --------------- Kiểm tra với HealtApp --------------- #
template_compare, structured_df, parse_df = compare_templates(SETTING_PARAMS['Mac'])
print_template_compare_difference(template_compare)

Giai đoạn tiền xử lý:
Shape:  (100314, 10)
Số lượng template:  626


Processing templates: 100%|██████████| 626/626 [00:03<00:00, 202.28it/s]


No. 7
Length: 1, Nums: 57
Ground truth  : IOHibernatePollerOpen(<*>)
Parse templs  : ['IOHibernatePollerOpen(0)']
Length parse: 1
----------------------------------------
No. 8
Length: 1, Nums: 2
Ground truth  : NSAllowAppKitWeakReferences=<*>
Parse templs  : ['NSAllowAppKitWeakReferences=YES']
Length parse: 1
----------------------------------------
No. 11
Length: 1, Nums: 137
Ground truth  : kern_open_file_for_direct_io(<*>)
Parse templs  : ['kern_open_file_for_direct_io(0)']
Length parse: 1
----------------------------------------
No. 12
Length: 1, Nums: 2
Ground truth  : newHeight=<*>,oldHeight=<*>
Parse templs  : ['newHeight=5421.000000,oldHeight=5421.000000', 'newHeight=990.000000,oldHeight=5452.000000']
Length parse: 2
----------------------------------------
No. 17
Length: 2, Nums: 5
Ground truth  : <*> STOP
Parse templs  : ['en0 STOP']
Length parse: 1
----------------------------------------
No. 18
Length: 2, Nums: 114
Ground truth  : AppleActuatorDevice::<*> Entered
Parse tem